In [1]:
import os
import scrapy
from scrapy.crawler import CrawlerProcess
import pandas as pd
from pathlib import Path
import json

In [2]:
absPath = str(Path(os.path.abspath(os.getcwd())).absolute())
datasetsPath = os.path.join(absPath, "raw_datasets")
gamesPath  = datasetsPath + "\games.csv"
games = pd.read_csv(gamesPath)
ids = games['id'].tolist()


In [3]:
print("Retrieving completion time for "+str(len(ids))+ " games")

class HLTB(scrapy.Spider):
    name = "hltb"
    #start_urls = [
    #    'https://howlongtobeat.com/game/66630'
    #]
    def start_requests(self):
        global ids
        #page_range = range(min_page, max_page+1)
        for i in ids:
            page_url = 'https://howlongtobeat.com/game/' + str(i)
            # print("Parsing search page:", page_id)
            yield scrapy.Request(url=page_url, callback=self.parse)
    
    def parse(self, response):
        title_id = response.url.split('/')[-1]
        #print(response.body)
        data = response.css('#__NEXT_DATA__::text').extract()[0]
        j=json.loads(data)
        
        #print(j["props"]["pageProps"]["game"]["data"]["platformData"])
        data = j["props"]["pageProps"]["game"]["data"]["platformData"]
        df_temp = pd.read_json(json.dumps(data))
        new_column = []
        for i in range(len(df_temp)):
            new_column.append(title_id)
        df_temp.insert(loc=0, column='gameID', value=new_column)
        #df_temp.columns = df_temp.loc[0]
        #df_temp = df_temp.drop(0)
        #df_temp.reset_index(drop=True)
        global df_merge
        df_merge = pd.concat([df_merge,df_temp],ignore_index=True,sort=False)

df_merge = pd.DataFrame()
process = scrapy.crawler.CrawlerProcess({'USER_AGENT':'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/88.0.4324.182 Safari/537.36'})
process.crawl(HLTB)
process.start()
df_merge.to_csv(datasetsPath+"\completion_time.csv",index=False)

2022-10-30 15:29:54 [scrapy.utils.log] INFO: Scrapy 2.6.2 started (bot: scrapybot)
2022-10-30 15:29:54 [scrapy.utils.log] INFO: Versions: lxml 4.9.1.0, libxml2 2.9.14, cssselect 1.1.0, parsel 1.6.0, w3lib 1.21.0, Twisted 22.2.0, Python 3.9.13 (main, Aug 25 2022, 23:51:50) [MSC v.1916 64 bit (AMD64)], pyOpenSSL 22.0.0 (OpenSSL 1.1.1q  5 Jul 2022), cryptography 37.0.1, Platform Windows-10-10.0.19045-SP0
2022-10-30 15:29:54 [scrapy.crawler] INFO: Overridden settings:
{'USER_AGENT': 'Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 '
               '(KHTML, like Gecko) Chrome/88.0.4324.182 Safari/537.36'}
2022-10-30 15:29:54 [scrapy.utils.log] DEBUG: Using reactor: twisted.internet.selectreactor.SelectReactor
2022-10-30 15:29:54 [scrapy.extensions.telnet] INFO: Telnet Password: e79a16166afe7c5c
2022-10-30 15:29:54 [scrapy.middleware] INFO: Enabled extensions:
['scrapy.extensions.corestats.CoreStats',
 'scrapy.extensions.telnet.TelnetConsole',
 'scrapy.extensions.logstats.LogSta

Retrieving completion time for 35922 games


2022-10-30 15:29:55 [scrapy.middleware] INFO: Enabled downloader middlewares:
['scrapy.downloadermiddlewares.httpauth.HttpAuthMiddleware',
 'scrapy.downloadermiddlewares.downloadtimeout.DownloadTimeoutMiddleware',
 'scrapy.downloadermiddlewares.defaultheaders.DefaultHeadersMiddleware',
 'scrapy.downloadermiddlewares.useragent.UserAgentMiddleware',
 'scrapy.downloadermiddlewares.retry.RetryMiddleware',
 'scrapy.downloadermiddlewares.redirect.MetaRefreshMiddleware',
 'scrapy.downloadermiddlewares.httpcompression.HttpCompressionMiddleware',
 'scrapy.downloadermiddlewares.redirect.RedirectMiddleware',
 'scrapy.downloadermiddlewares.cookies.CookiesMiddleware',
 'scrapy.downloadermiddlewares.httpproxy.HttpProxyMiddleware',
 'scrapy.downloadermiddlewares.stats.DownloaderStats']
2022-10-30 15:29:55 [scrapy.middleware] INFO: Enabled spider middlewares:
['scrapy.spidermiddlewares.httperror.HttpErrorMiddleware',
 'scrapy.spidermiddlewares.offsite.OffsiteMiddleware',
 'scrapy.spidermiddlewares.ref